In [117]:
import os
import  keras
keras.__version__ 

'1.2.2'

In [118]:
FN = 'train'
FN0 = 'vocab-embedding'
FN1 ='train' 

In [119]:
maxlend=100 # 0 - if we dont want to use description at all
maxlenh=15
maxlen = maxlend + maxlenh
rnn_size = 512 # must be same as 160330-word-gen
rnn_layers = 3  # match FN1
batch_norm=False

In [120]:
activation_rnn_size = 40 if maxlend else 0

In [121]:
# training parameters
seed=44
p_W, p_U, p_dense, p_emb, weight_decay = 0, 0, 0, 0, 0
optimizer = 'adam'
LR = 1e-4
batch_size=80
nflips=10

In [122]:
import pickle as pickle
with open('%s.pkl'%FN0, 'rb') as fp:
    embedding, idx2word, word2idx, glove_idx2idx = pickle.load(fp)
vocab_size, embedding_size = embedding.shape

In [123]:
with open('%s.data.pkl'%FN0, 'rb') as fp:
    X, Y = pickle.load(fp)

In [124]:
nb_unknown_words = 10

In [125]:
X

[[2666,
  121,
  741,
  52,
  3433,
  378,
  3505,
  378,
  20,
  46,
  304,
  605,
  6781,
  2746,
  3,
  9,
  2,
  101,
  95,
  3,
  358,
  25,
  28,
  381,
  2,
  83,
  37,
  10,
  75,
  48,
  5,
  2,
  342,
  802,
  7,
  907,
  6782,
  25,
  121,
  5,
  168,
  619,
  350,
  945,
  6,
  627,
  2249,
  121,
  6781,
  12,
  614,
  348,
  121,
  636,
  3,
  25,
  8,
  378,
  42,
  7589,
  21,
  48,
  147,
  1198,
  37,
  3434,
  4,
  378,
  3150,
  20,
  3433,
  6436,
  6,
  354,
  210,
  9,
  2956,
  52,
  3433,
  12,
  13,
  570,
  11,
  8,
  75,
  1975,
  5,
  441,
  1052,
  907,
  22,
  8,
  230,
  350,
  201,
  2956,
  36,
  17,
  2844,
  2186,
  8,
  352,
  2187,
  7,
  2,
  614,
  348,
  378,
  42,
  954,
  54,
  7,
  2,
  9385,
  101,
  348,
  215,
  2,
  76,
  12,
  2956,
  4712,
  378,
  114,
  5897,
  2089,
  636,
  13,
  2,
  96,
  5,
  2051,
  350,
  1976,
  840,
  8,
  351,
  3,
  320,
  2187,
  21,
  1100,
  2,
  298,
  93,
  435,
  3,
  6781,
  350,
  548,
  6,
  23,
  

In [126]:
print ('number of examples',len(X),len(Y))
print ('dimension of embedding space for words',embedding_size)
print ('vocabulary size', vocab_size, 'the last %d words can be used as place holders for unknown/oov words'%nb_unknown_words)
print ('total number of different words',len(idx2word), len(word2idx))
print ('number of words outside vocabulary which we can substitue using glove similarity', len(glove_idx2idx))
print ('number of words that will be regarded as unknonw(unk)/out-of-vocabulary(oov)',len(idx2word)-vocab_size-len(glove_idx2idx))

number of examples 2225 2225
dimension of embedding space for words 100
vocabulary size 25003 the last 10 words can be used as place holders for unknown/oov words
total number of different words 25003 25003
number of words outside vocabulary which we can substitue using glove similarity 15
number of words that will be regarded as unknonw(unk)/out-of-vocabulary(oov) -15


In [127]:
for i in range(nb_unknown_words):
    idx2word[vocab_size-1-i] = '<%d>'%i

In [128]:
oov0 = vocab_size-nb_unknown_words
for i in range(oov0, len(idx2word)):
    idx2word[i] = idx2word[i]+'^'

In [129]:
nb_train_samples = 2000
nb_val_samples = 222
from sklearn.cross_validation import train_test_split
X_train, X_test, Y_train, Y_test = train_test_split(X, Y, test_size=nb_val_samples, random_state=seed)
len(X_train), len(Y_train), len(X_test), len(Y_test)

(2003, 2003, 222, 222)

In [130]:
Y_train

[[15,
  12,
  2,
  513,
  37,
  23,
  16,
  327,
  2150,
  7,
  2,
  118,
  28,
  23,
  16,
  49,
  2,
  8104,
  5,
  507,
  407,
  6,
  132,
  11,
  23,
  275,
  45,
  2,
  1731,
  3,
  68,
  40,
  18,
  92,
  244,
  6,
  668,
  2,
  3915,
  1130,
  11,
  50,
  32,
  16,
  621,
  401,
  132,
  1205,
  3,
  990,
  7,
  2,
  571,
  28,
  2,
  6094,
  5,
  35,
  28,
  115,
  23,
  16,
  13,
  132,
  37,
  199,
  45,
  7,
  439,
  5,
  1541,
  507,
  77,
  31,
  61,
  923,
  1831,
  3,
  6,
  990,
  79,
  31,
  130,
  13,
  407,
  124,
  52,
  2804,
  11,
  1205,
  10,
  1130,
  3,
  559,
  235,
  3,
  3915,
  265,
  18,
  3872,
  5628,
  5,
  261,
  132,
  197,
  3,
  1442,
  21,
  384,
  7,
  261,
  1275,
  6,
  509,
  36,
  4,
  5536,
  28,
  7,
  235,
  3,
  249,
  499,
  21,
  2440,
  1884,
  2,
  3915,
  13,
  545,
  1059,
  5,
  132,
  2788,
  6,
  209,
  898,
  19,
  2516,
  7,
  1212,
  2789,
  9,
  2,
  649,
  261,
  1275,
  115,
  2440,
  2,
  797,
  35,
  28,
  940,
  58,
  49

In [131]:
del X
del Y

In [132]:
empty = 0
eos = 1
idx2word[empty] = '_'
idx2word[eos] = '~'

In [133]:
import  numpy  as  npnp
from  keras.preprocessing  import sequence
from keras.utils import np_utils
import random, sys

In [134]:
def prt(label, word_idx,idx2word):
    words = [idx2word[word] for word in word_idx]
    print('{}: {}\n'.format(label, ' '.join(words)))

In [135]:
i = 334
prt('H',Y_train[i],idx2word)
prt('D',X_train[i],idx2word)

H: although the two partially paralysed people performed better overall the researcher said this could be because their brain were more used to adapting or that they were simply more motivated a team of u researcher ha shown that controlling device with the brain is a step closer earlier this year a team at the mit medium lab europe demonstrated a wireless cap which read brain wave to control a computer character four people two of them partly paralysed wheelchair user successfully moved a computer cursor while wearing a cap with electrode previous research ha shown that monkey can control a computer with electrode implanted into their brain the research team from new york state department of health and state university of new york in albany said the research wa another step towards people controlling wheelchair or other electronic device by thought such brain activity doe not require the use of any nerve of muscle so people with stroke or spinal cord injury could use the cap effective

In [136]:
i = 22
prt('H',Y_test[i],idx2word)
prt('D',X_test[i],idx2word)

H: he had lost three time to roddick and this wa his day to beat him some people have said that i am obsessed but i think that it is better this way spain victory wa also remarkable for the performance of rafael nadal who beat roddick in the opening single carlos moya described spain davis cup victory a the highlight of his career after he beat andy roddick to end the usa challenge in seville spain only other davis cup title came two year ago in valencia when they beat australia and moya nicknamed charly admitted the davis cup is my dream and i wa a bit nervous at the outset what a great way to finish the year said nadal afterwards but certainly i think we can put the work in at the appropriate time and play a couple more event and play against these guy who are the best on this stuff said mcenroe roddick wa left frustrated after losing both his single on the slow clay of seville olympic stadium it just tough because i felt like i wa in it the whole time against one of the top three cl

In [137]:
from keras.models import Sequential
from keras.layers.core import Dense, Activation, Dropout, RepeatVector
from keras.layers.wrappers import TimeDistributed
from keras.layers.recurrent import LSTM
from keras.layers.embeddings import Embedding
from keras.regularizers import l2
from keras.layers import merge

In [138]:
import numpy as np
# seed weight initialization# seed w 
random.seed(seed)
np.random.seed(seed)

In [139]:
regularizer= l2(weight_decay) if weight_decay else None

In [140]:
model = Sequential()
model.add(Embedding(vocab_size, embedding_size,
                    input_length=maxlen,
                    W_regularizer=regularizer, dropout=p_emb, weights=[embedding], mask_zero=True,
                    name='embedding_1'))
for i in range(rnn_layers):
    lstm = LSTM(rnn_size, return_sequences=True, # batch_norm=batch_norm,
                W_regularizer=regularizer, U_regularizer=regularizer,
                b_regularizer=regularizer, dropout_W=p_W, dropout_U=p_U,
                name='lstm_{}'.format(i + 1)
                  )
    model.add(lstm)
    model.add(Dropout(p_dense, name='dropout_{}'.format(i + 1)))

In [141]:
from keras.layers.core import Lambda
import keras.backend as K

def simple_context(X, mask, n=activation_rnn_size,maxlend=maxlend, maxlenh=maxlenh):
    desc, head = X[:,:maxlend,:], X[:,maxlend:,:]
    head_activations, head_words = head[:,:,:n], head[:,:,n:]
    desc_activations, desc_words = desc[:,:,:n], desc[:,:,n:]
    
    # RTFM http://deeplearning.net/software/theano/library/tensor/basic.html#theano.tensor.batched_tensordot
    # activation for every head word and every desc word
    activation_energies = K.batch_dot(head_activations, desc_activations, axes=(2,2))
    # make sure we dont use description words that are masked out
    activation_energies = activation_energies+ -1e20*K.expand_dims(1.-K.cast(mask[:, :maxlend],'float32'),1)
    
    # for every head word compute weights for every desc word
    activation_energies = K.reshape(activation_energies,(-1,maxlend))
    activation_weights = K.softmax(activation_energies)
    activation_weights = K.reshape(activation_weights,(-1,maxlenh,maxlend))

    # for every head word compute weighted average of desc words
    desc_avg_word = K.batch_dot(activation_weights, desc_words, axes=(2,1))
    return K.concatenate((desc_avg_word, head_words))


class SimpleContext(Lambda):
    def __init__(self,fn, rnn_size,**kwargs):
        """Initialize SimpleContext."""
        self.rnn_size = rnn_size
        super(SimpleContext, self).__init__(fn, **kwargs)
        self.supports_masking = True

    def compute_mask(self, input, input_mask=None):
        return input_mask[:, maxlend:]
    
    def get_output_shape_for(self, input_shape):
        nb_samples = input_shape[0]
        n = 2*(rnn_size - activation_rnn_size)
        return (nb_samples, maxlenh, n)

In [142]:
if activation_rnn_size:
    model.add(SimpleContext(simple_context, rnn_size, name='simplecontext_1'))

model.add(TimeDistributed(Dense(vocab_size,
                                W_regularizer=regularizer, b_regularizer=regularizer,
                                name = 'timedistributed_1')))

model.add(Activation('softmax', name='activation_1'))

In [143]:
from  keras.optimizers  import Adam, RMSprop # usually I prefer Adam but article used rmsprop
# opt = Adam(lr=LR)  # keep calm and reduce learning rate
model.compile(loss='categorical_crossentropy', optimizer=optimizer)

In [144]:
%%javascript
// new Audio("http://www.soundjay.com/button/beep-09.wav").play ()

<IPython.core.display.Javascript object>

In [145]:
K.set_value(model.optimizer.lr,np.float32(LR))

In [146]:
def str_shape(x):
    return 'x'.join(map(str,x.shape))
    
def inspect_model(model):
    for i,l in enumerate(model.layers):
        print (i, 'cls=%s name=%s'%(type(l).__name__, l.name))
        weights = l.get_weights()
        for weight in weights:
            print (str_shape(weight),)
        print()

In [147]:
inspect_model(model)

0 cls=Embedding name=embedding_1
25003x100

1 cls=LSTM name=lstm_1
100x512
512x512
512
100x512
512x512
512
100x512
512x512
512
100x512
512x512
512

2 cls=Dropout name=dropout_1

3 cls=LSTM name=lstm_2
512x512
512x512
512
512x512
512x512
512
512x512
512x512
512
512x512
512x512
512

4 cls=Dropout name=dropout_2

5 cls=LSTM name=lstm_3
512x512
512x512
512
512x512
512x512
512
512x512
512x512
512
512x512
512x512
512

6 cls=Dropout name=dropout_3

7 cls=SimpleContext name=simplecontext_1

8 cls=TimeDistributed name=timedistributed_3
944x25003
25003

9 cls=Activation name=activation_1



In [148]:
if FN1 and os.path.exists('data/%s.hdf5'%FN1):
    model.load_weights('data/%s.hdf5'%FN1)

In [149]:
def lpadd(x, maxlend=maxlend, eos=eos):
    """left (pre) pad a description to maxlend and then add eos.
    The eos is the input to predicting the first word in the headline
    """
    assert maxlend >= 0
    if maxlend == 0:
        return [eos]
    n = len(x)
    if n > maxlend:
        x = x[-maxlend:]
        n = maxlend
    return [empty]*(maxlend-n) + x + [eos]

In [150]:
samples = [lpadd([3]*26)]
# pad from right (post) so the first maxlend will be description followed by headline
data = sequence.pad_sequences(samples, maxlen=maxlen, value=empty, padding='post', truncating='post')

In [151]:
np.all(data[:,maxlend] == eos)

True

In [152]:
data.shape,list(map(len, samples))

((1, 115), [101])

In [153]:
probs = model.predict(data, verbose=0, batch_size=1)
probs.shape

(1, 15, 25003)

In [154]:
# variation to https://github.com/ryankiros/skip-thoughts/blob/master/decoding/search.py
def beamsearch(predict, start=[empty]*maxlend + [eos],
               k=1, maxsample=maxlen, use_unk=True, empty=empty, eos=eos, temperature=1.0):
    """return k samples (beams) and their NLL scores, each sample is a sequence of labels,
    all samples starts with an `empty` label and end with `eos` or truncated to length of `maxsample`.
    You need to supply `predict` which returns the label probability of each sample.
    `use_unk` allow usage of `oov` (out-of-vocabulary) label in samples
    """
    def sample(energy, n, temperature=temperature):
        """sample at most n elements according to their energy"""
        n = min(n,len(energy))
        prb = np.exp(-np.array(energy) / temperature )
        res = []
        for i in range(n):
            z = np.sum(prb)
            r = np.argmax(np.random.multinomial(1, prb/z, 1))
            res.append(r)
            prb[r] = 0. # make sure we select each element only once
        return res

    dead_k = 0 # samples that reached eos
    dead_samples = []
    dead_scores = []
    live_k = 1 # samples that did not yet reached eos
    live_samples = [list(start)]
    live_scores = [0]

    while live_k:
        # for every possible live sample calc prob for every possible label 
        probs = predict(live_samples, empty=empty)

        # total score for every sample is sum of -log of word prb
        cand_scores = np.array(live_scores)[:,None] - np.log(probs)
        cand_scores[:,empty] = 1e20
        if not use_unk:
            for i in range(nb_unknown_words):
                cand_scores[:,vocab_size - 1 - i] = 1e20
        live_scores = list(cand_scores.flatten())
        

        # find the best (lowest) scores we have from all possible dead samples and
        # all live samples and all possible new words added
        scores = dead_scores + live_scores
        ranks = sample(scores, k)
        n = len(dead_scores)
        ranks_dead = [r for r in ranks if r < n]
        ranks_live = [r - n for r in ranks if r >= n]
        
        dead_scores = [dead_scores[r] for r in ranks_dead]
        dead_samples = [dead_samples[r] for r in ranks_dead]
        
        live_scores = [live_scores[r] for r in ranks_live]

        # append the new words to their appropriate live sample
        voc_size = probs.shape[1]
        live_samples = [live_samples[r//voc_size]+[r%voc_size] for r in ranks_live]

        # live samples that should be dead are...
        # even if len(live_samples) == maxsample we dont want it dead because we want one
        # last prediction out of it to reach a headline of maxlenh
        zombie = [s[-1] == eos or len(s) > maxsample for s in live_samples]
        
        # add zombies to the dead
        dead_samples += [s for s,z in zip(live_samples,zombie) if z]
        dead_scores += [s for s,z in zip(live_scores,zombie) if z]
        dead_k = len(dead_samples)
        # remove zombies from the living 
        live_samples = [s for s,z in zip(live_samples,zombie) if not z]
        live_scores = [s for s,z in zip(live_scores,zombie) if not z]
        live_k = len(live_samples)

    return dead_samples + live_samples, dead_scores + live_scores

In [155]:
def keras_rnn_predict(samples, empty=empty, model=model, maxlen=maxlen):
    """for every sample, calculate probability for every possible label
    you need to supply your RNN model and maxlen - the length of sequences it can handle
    """
    sample_lengths = list(map(len, samples))
    assert all(l > maxlend for l in sample_lengths)
    assert all(l[maxlend] == eos for l in samples)
    # pad from right (post) so the first maxlend will be description followed by headline
    data = sequence.pad_sequences(samples, maxlen=maxlen, value=empty, padding='post', truncating='post')
    probs = model.predict(data, verbose=0, batch_size=batch_size)
    return np.array([prob[sample_length-maxlend-1] for prob, sample_length in zip(probs, sample_lengths)])

In [156]:
def vocab_fold(xs, oov0, glove_idx2idx, vocab_size, nb_unknown_words):
    """Convert list of word indices that may contain words outside vocab_size to words inside.
    If a word is outside, try first to use glove_idx2idx to find a similar word inside.
    If none exist then replace all accurancies of the same unknown word with <0>, <1>, ...
    """
    xs = [x if x < oov0 else glove_idx2idx.get(x, x) for x in xs]
    # the more popular word is <0> and so on
    outside = sorted([x for x in xs if x >= oov0])
    # if there are more than nb_unknown_words oov words then put them all in nb_unknown_words-1
    outside = dict((x, vocab_size - 1 - min(i, nb_unknown_words - 1)) for i, x in enumerate(outside))
    xs = [outside.get(x, x) for x in xs]
    return xs

In [157]:
def  vocab_unfold (desc,xs):
    # assume desc is the unfolded version of the start of xs
    unfold = {}
    for i, unfold_idx in enumerate(desc):
        fold_idx = xs[i]
        if fold_idx >= oov0:
            unfold[fold_idx] = unfold_idx
    return [unfold.get(x,x) for x in xs]

In [158]:
import sys
import Levenshtein

def gensamples(skips=2, k=10, batch_size=batch_size, short=True, temperature=1., use_unk=True):
    i = random.randint(0,len(X_test)-1)
    print ('HEAD:',' '.join(idx2word[w] for w in Y_test[i][:maxlenh]))
    print ('DESC:',' '.join(idx2word[w] for w in X_test[i][:maxlend]))
    sys.stdout.flush()

    print ('HEADS:')
    x = X_test[i]
    samples = []
    if maxlend == 0:
        skips = [0]
    else:
        skips = range(min(maxlend,len(x)), max(maxlend,len(x)), abs(maxlend - len(x)) // skips + 1)
    for s in skips:
        start = lpadd(x[:s])
        fold_start = vocab_fold(start,oov0, glove_idx2idx, vocab_size, nb_unknown_words)
        sample, score = beamsearch(predict=keras_rnn_predict, start=fold_start, k=k, temperature=temperature, use_unk=use_unk)
        assert all(s[maxlend] == eos for s in sample)
        samples += [(s,start,scr) for s,scr in zip(sample,score)]

    samples.sort(key=lambda x: x[-1])
    codes = []
    for sample, start, score in samples:
        code = ''
        words = []
        sample = vocab_unfold(start, sample)[len(start):]
        for w in sample:
            if w == eos:
                break
            words.append(idx2word[w])
            code += chr(w//(256*256)) + chr((w//256)%256) + chr(w%256)
        if short:
            distance = min([100] + [-Levenshtein.jaro(code,c) for c in codes])
            if distance > -0.6:
                print (score, ' '.join(words))
        #         print '%s (%.2f) %f'%(' '.join(words), score, distance)
        else:
                print (score, ' '.join(words))
        codes.append(code)

In [159]:
gensamples(skips=2, batch_size=batch_size, k=10, temperature=1.)

HEAD: almost of those questioned said they would trust search engine much le if they knew
DESC: savvy searcher fail to spot ad internet search engine user are an odd mix of naive and sophisticated suggests a report into search habit the report by the u pew research center reveals that of searcher usually find what they were looking for when using a search engine it also show that few can spot the difference between paid for result and organic one the report reveals that of net user say they regularly use google ask jeeves msn and yahoo when online almost of those questioned said they would trust search engine much le if they knew information about
HEADS:
151.7090768814087 allahgreen authoritarian am poorly rapport guilt recess suspicious bayleaf crisp reboot evans consenus owns tok
151.86193466186523 householder artificially prater grind crabbe shift cohesion wiedersehen claret arch sufficiently clement converse sexually restart
151.92283821105957 indexed notignore crop waited superint

In [160]:
def flip_headline(x, nflips, model, debug, oov0, idx2word):
    """Flip some of the words in the second half (headline) with words predicted by the model."""
    if nflips is None or model is None or nflips <= 0:
        return x

    batch_size = len(x)
    assert np.all(x[:, maxlend] == eos)
    probs = model.predict(x, verbose=0, batch_size=batch_size)
    x_out = x.copy()
    for b in range(batch_size):
        # pick locations we want to flip
        # 0...maxlend-1 are descriptions and should be fixed
        # maxlend is eos and should be fixed
        flips = sorted(random.sample(range(maxlend + 1, maxlen), nflips))
        if debug and b < debug:
            print(b)
        for input_idx in flips:
            if x[b, input_idx] == empty or x[b, input_idx] == eos:
                continue
            # convert from input location to label location
            # the output at maxlend (when input is eos) is feed as input at maxlend+1
            label_idx = input_idx - (maxlend + 1)
            prob = probs[b, label_idx]
            w = prob.argmax()
            if w == empty:  # replace accidental empty with oov
                w = oov0
            if debug and b < debug:
                print('{} => {}'.format(idx2word[x_out[b, input_idx]], idx2word[w]),)
            x_out[b, input_idx] = w
        if debug and b < debug:
            print()
    return x_out

In [161]:
def conv_seq_labels(xds, xhs, nflips, model, debug, oov0, glove_idx2idx, vocab_size, nb_unknown_words, idx2word):
    """Convert description and hedlines to padded input vectors; headlines are one-hot to label."""
    batch_size = len(xhs)
    assert len(xds) == batch_size
    x = [
        vocab_fold(lpadd(xd) + xh, oov0, glove_idx2idx, vocab_size, nb_unknown_words)
        for xd, xh in zip(xds, xhs)]  # the input does not have 2nd eos
    x = sequence.pad_sequences(x, maxlen=maxlen, value=empty, padding='post', truncating='post')
    x = flip_headline(x, nflips=nflips, model=model, debug=debug, oov0=oov0, idx2word=idx2word)

    y = np.zeros((batch_size, maxlenh, vocab_size))
    for i, xh in enumerate(xhs):
        xh = vocab_fold(xh, oov0, glove_idx2idx, vocab_size, nb_unknown_words) + [eos] + [empty] * maxlenh  # output does have a eos at end
        xh = xh[:maxlenh]
        y[i, :, :] = np_utils.to_categorical(xh, vocab_size)

    return x, y

In [162]:
def gen(Xd, Xh, batch_size, nb_batches, nflips, model, debug, oov0, glove_idx2idx, vocab_size, nb_unknown_words, idx2word):
    """Yield batches.
    for training use nb_batches=None
    for validation generate deterministic results repeating every nb_batches
    """
    # while training it is good idea to flip once in a while the values of the headlines from the
    # value taken from Xh to value generated by the model.
    c = nb_batches if nb_batches else 0
    while True:
        xds = []
        xhs = []
        if nb_batches and c >= nb_batches:
            c = 0
        new_seed = random.randint(0, 2e10)
        random.seed(c + 123456789 + seed)
        for b in range(batch_size):
            t = random.randint(0, len(Xd) - 1)

            xd = Xd[t]
            s = random.randint(min(maxlend, len(xd)), max(maxlend, len(xd)))
            xds.append(xd[:s])

            xh = Xh[t]
            s = random.randint(min(maxlenh, len(xh)), max(maxlenh, len(xh)))
            xhs.append(xh[:s])

        # undo the seeding before we yield inorder not to affect the caller
        c += 1
        random.seed(new_seed)

        yield conv_seq_labels(
            xds,
            xhs,
            nflips=nflips,
            model=model,
            debug=debug,
            oov0=oov0,
            glove_idx2idx=glove_idx2idx,
            vocab_size=vocab_size,
            nb_unknown_words=nb_unknown_words,
            idx2word=idx2word,
        )

In [163]:
r = next(gen(X_train, Y_train, batch_size=batch_size, nb_batches=None, nflips=None, model=None, debug=False, oov0=oov0, glove_idx2idx=glove_idx2idx, vocab_size=vocab_size, nb_unknown_words=nb_unknown_words, idx2word=idx2word))
r[0].shape, r[1].shape, len(r)

((80, 115), (80, 15, 25003), 2)

In [164]:
def test_gen(gen, n=5):
    Xtr,Ytr = next(gen)
    for i in range(n):
        assert Xtr[i,maxlend] == eos
        x = Xtr[i,:maxlend]
        y = Xtr[i,maxlend:]
        yy = Ytr[i,:]
        yy = np.where(yy)[1]
        prt('L',yy,idx2word)
        prt('H',y,idx2word)
        if maxlend:
            prt('D',x,idx2word)

In [165]:
test_gen(gen(X_train, Y_train, batch_size=batch_size, nb_batches=None, nflips=None, model=None, debug=False, oov0=oov0, glove_idx2idx=glove_idx2idx, vocab_size=vocab_size, nb_unknown_words=nb_unknown_words, idx2word=idx2word))

L: viotti director of la fenice since conducted at renowned opera house worldwide including milan la

H: ~ viotti director of la fenice since conducted at renowned opera house worldwide including milan

D: la fenice viotti wa widely acclaimed for his production of the french composer massenet thai and some of his other production included giuseppe verdi la traviata and richard strauss ariadne auf naxos the last opera he directed at la fenice wa massenet le roi de lahore viotti debut at the new york metropolitan opera came in with giacomo puccini madame butterfly followed by la boheme la traviata and fromental halevy la juive giampaolo vianello superintendent of the fenice theatre foundation said i am filled with extreme sadness because other than a great artist he is missed a a friend a

L: rico gear ran in two of the all black seven try in what wa a

H: ~ rico gear ran in two of the all black seven try in what wa

D: match wa blighted by controversy moment later when justin marshall w

In [166]:
test_gen(gen(X_train, Y_train, batch_size=batch_size, nb_batches=None, nflips=6, model=None, debug=False, oov0=oov0, glove_idx2idx=glove_idx2idx, vocab_size=vocab_size, nb_unknown_words=nb_unknown_words, idx2word=idx2word))

L: viotti director of la fenice since conducted at renowned opera house worldwide including milan la

H: ~ viotti director of la fenice since conducted at renowned opera house worldwide including milan

D: la fenice viotti wa widely acclaimed for his production of the french composer massenet thai and some of his other production included giuseppe verdi la traviata and richard strauss ariadne auf naxos the last opera he directed at la fenice wa massenet le roi de lahore viotti debut at the new york metropolitan opera came in with giacomo puccini madame butterfly followed by la boheme la traviata and fromental halevy la juive giampaolo vianello superintendent of the fenice theatre foundation said i am filled with extreme sadness because other than a great artist he is missed a a friend a

L: rico gear ran in two of the all black seven try in what wa a

H: ~ rico gear ran in two of the all black seven try in what wa

D: match wa blighted by controversy moment later when justin marshall w

In [167]:
valgen = gen(X_test, Y_test, batch_size=batch_size, nb_batches=nb_val_samples // batch_size, nflips=None, model=None, debug=False, oov0=oov0, glove_idx2idx=glove_idx2idx, vocab_size=vocab_size, nb_unknown_words=nb_unknown_words, idx2word=idx2word)

In [168]:
for i in range(4):
    test_gen(valgen, n=1)

L: writer tony cowell is among the judge who will hear aspiring writer read their work

H: ~ writer tony cowell is among the judge who will hear aspiring writer read their

D: a public vote will also take place which will account for of the final decision the winner will be announced at the london book fair on march next year and could be screened on tv it very very hard to find an agent and extremely difficult without an agent to get a publisher to look at your work said cowell people do fall by the wayside and the more avenue we can provide for aspiring author the better he added paul cavanagh a former university professor and health care consultant from ontario in canada wa one of aspiring novelist to

L: the release of a film about the mumbai bombay blast in ha been postponed following

H: ~ the release of a film about the mumbai bombay blast in ha been postponed

D: they previously asked that a line from the movie poster which claimed the film portrayed the true story of the bomba

In [169]:
history = {}

In [170]:
valgen = gen(X_test, Y_test, batch_size=batch_size, nb_batches=nb_val_samples // batch_size, nflips=None, 
             model=None, debug=False, oov0=oov0, glove_idx2idx=glove_idx2idx, vocab_size=vocab_size, 
             nb_unknown_words=nb_unknown_words, idx2word=idx2word)
traingen=gen(X_train, Y_train, batch_size=batch_size, nb_batches=None, nflips=nflips, 
             model=model, debug=False, oov0=oov0, glove_idx2idx=glove_idx2idx, vocab_size=vocab_size, 
             nb_unknown_words=nb_unknown_words, idx2word=idx2word)


In [171]:
r = next(gen(X_train, Y_train, batch_size=batch_size, nb_batches=None, nflips=None, model=None, debug=False, oov0=oov0, glove_idx2idx=glove_idx2idx, vocab_size=vocab_size, nb_unknown_words=nb_unknown_words, idx2word=idx2word))
r[0].shape, r[1].shape, len(r)

((80, 115), (80, 15, 25003), 2)

In [172]:
for iteration in range(500):
    print ('Iteration', iteration)
    h = model.fit_generator(traingen, samples_per_epoch=nb_train_samples,
                        nb_epoch=1, validation_data=valgen, nb_val_samples=nb_val_samples
                           )
    for k,v in h.history.items():
        history[k] = history.get(k,[]) + v
    with open('%s.history.pkl'%FN,'wb') as fp:
        pickle.dump(history,fp,-1)
    model.save_weights('%s.hdf5'%FN, overwrite=True)
    gensamples(batch_size=batch_size)

Iteration 0
Epoch 1/1
2000/2000 [==============================] - 939s - loss: 9.3837 - val_loss: 8.1425
HEAD: an ogara penalty put ireland more than a converted try ahead and they made the
DESC: italy ireland two moment of magic from brian odriscoll guided ireland to a workmanlike victory against italy a pair of classic outside break from the ireland captain set up try for geordan murphy and peter stringer italy led early in the second half but stringer try gave ireland a lead they never lost the host cut the gap to with minute left and nearly scored through ludovico nitoglia but denis hickie try ensured an irish victory italy came flying out of the block and took the lead through a luciano orquera penalty after seven minute it could have been better
HEADS:
119.15014791488647 uk consumer film thomas company ha box many band earlier mike between d asia than
126.5670862197876 rouble net monday billy gdp learning exchange in gage have music rise yelena response play
Iteration 1
Epoch 1/

HEADS:
57.26019525527954 said the from wa for the the to the the set the the mr wa
Iteration 10
Epoch 1/1
2000/2000 [==============================] - 1217s - loss: 6.8305 - val_loss: 7.1708
HEAD: excluding the car sector u retail sale were up in january twice what some analyst
DESC: car pull down u retail figure u retail sale fell in january the biggest monthly decline since last august driven down by a heavy fall in car sale the fall in car sale had been expected coming after december rise in car sale fuelled by generous pre christmas special offer excluding the car sector u retail sale were up in january twice what some analyst had been expecting u retail spending is expected to rise in but not a quickly a in steve gallagher u chief economist at sg corporate investment banking said january figure were decent number we are
HEADS:
51.95140981674194 the the the a a at the in to the the wa in and the
Iteration 11
Epoch 1/1
2000/2000 [==============================] - 1239s - loss: 6.777

KeyboardInterrupt: 